## Init NLTK

In [15]:
import nltk
import numpy
from nltk.stem.snowball import SnowballStemmer
from nltk.corpus import stopwords
import string

In [2]:
nltk.download()

showing info https://raw.githubusercontent.com/nltk/nltk_data/gh-pages/index.xml


True

In [9]:
sw = stopwords.words("english")
print len(sw)

153


## Parser

In [79]:
def parseOutText(f):
    """ given an opened email file f, parse out all text below the
        metadata block at the top
        (in Part 2, you will also add stemming capabilities)
        and return a string that contains all the words
        in the email (space-separated) 
        
        example use case:
        f = open("email_file_name.txt", "r")
        text = parseOutText(f)
        
        """


    f.seek(0)  ### go back to beginning of file (annoying)
    all_text = f.read()
    
    ### split off metadata
    content = all_text.split("X-FileName:")
  
    words = ""
    if len(content) > 1:
        ### remove punctuation
        text_string = content[1].translate(string.maketrans("", ""), string.punctuation)

        ### project part 2: comment out the line below
        # words = text_string

        ### split the text string into individual words, stem each word,
        ### and append the stemmed word to words (make sure there's a single
        ### space between each stemmed word)
        
        stemmer = SnowballStemmer("english")

        to_stem = text_string.replace('\n', ' ').split()
        words = " ".join([stemmer.stem(word) for word in to_stem])
        
        
        return words

## Try it out with a test email

In [80]:
ff = open(r"C:\Users\dehaeth\Documents\Tools\Python\Oefeningen\Udacity\Machine learning intor\ud120-projects-master\text_learning\test_email.txt", "r")
text = parseOutText(ff)
print text

hi everyon if you can read this messag your proper use parseouttext pleas proceed to the next part of the project


# Part 2: do it on a full email dataset

## Necessary imports

In [81]:
import os
import pickle
import re


## Run through emails and export features

In [128]:
### temp_counter is a way to speed up the development--there are
### thousands of emails from Sara and Chris, so running over all of them
### can take a long time
### temp_counter helps you only look at the first 200 emails in the list so you
### can iterate your modifications quicker
temp_counter = 0

def extract_rinse_repeat(naughtylist):
    
    from_sara  = open(r"C:\Users\dehaeth\Documents\Tools\Python\Oefeningen\Udacity\Machine learning intor\ud120-projects-master\text_learning\from_sara.txt", "r")
    from_chris = open(r"C:\Users\dehaeth\Documents\Tools\Python\Oefeningen\Udacity\Machine learning intor\ud120-projects-master\text_learning\from_chris.txt", "r")

    from_data = []
    word_data = []

    for name, from_person in [("sara", from_sara), ("chris", from_chris)]:
        for path in from_person:
            ### only look at first 200 emails when developing
            ### once everything is working, remove this line to run over full dataset
            if True:
                path = os.path.join(r'C:\Users\dehaeth\Documents\Tools\Python\Oefeningen\Udacity\Machine learning intor\ud120-projects-master', path[:-1])
                print path
                email = open(path, "r")

                ### use parseOutText to extract the text from the opened email
                ### use str.replace() to remove any instances of the words
                ### ["sara", "shackleton", "chris", "germani"]
                parsed_mail = parseOutText(email)

                signatures = naughtylist
                for word in signatures:
                    parsed_mail = parsed_mail.replace(word, "")

                word_data.append(parsed_mail)
                from_data.append(0 if name == "sara" else 1)

                email.close()


    print "emails processed"
    from_sara.close()
    from_chris.close()

    pickle.dump( word_data, open("your_word_data.pkl", "w") )
    pickle.dump( from_data, open("your_email_authors.pkl", "w") )

In [129]:
extract_rinse_repeat(["sara", "shackleton", "chris", "germani"])

print word_data[152]

C:\Users\dehaeth\Documents\Tools\Python\Oefeningen\Udacity\Machine learning intor\ud120-projects-master\maildir/bailey-s/deleted_items/101.
C:\Users\dehaeth\Documents\Tools\Python\Oefeningen\Udacity\Machine learning intor\ud120-projects-master\maildir/bailey-s/deleted_items/106.
C:\Users\dehaeth\Documents\Tools\Python\Oefeningen\Udacity\Machine learning intor\ud120-projects-master\maildir/bailey-s/deleted_items/132.
C:\Users\dehaeth\Documents\Tools\Python\Oefeningen\Udacity\Machine learning intor\ud120-projects-master\maildir/bailey-s/deleted_items/185.
C:\Users\dehaeth\Documents\Tools\Python\Oefeningen\Udacity\Machine learning intor\ud120-projects-master\maildir/bailey-s/deleted_items/186.
C:\Users\dehaeth\Documents\Tools\Python\Oefeningen\Udacity\Machine learning intor\ud120-projects-master\maildir/bailey-s/deleted_items/187.
C:\Users\dehaeth\Documents\Tools\Python\Oefeningen\Udacity\Machine learning intor\ud120-projects-master\maildir/bailey-s/deleted_items/193.
C:\Users\dehaeth\Doc

## Vectorize using TfIfd

In [130]:
from sklearn.feature_extraction.text import TfidfVectorizer
ti = TfidfVectorizer(stop_words='english')
ti.fit(word_data)
print len(ti.get_feature_names())
print ti.get_feature_names()[34597]

38756
stephanlonect


## Apply to enron email data

In [132]:
import numpy
numpy.random.seed(42)
words_file = "your_word_data.pkl" 
authors_file = "your_email_authors.pkl"
word_data = pickle.load( open(words_file, "r"))
authors = pickle.load( open(authors_file, "r") )

## Create train and test set

In [133]:
from sklearn import cross_validation
features_train, features_test, labels_train, labels_test = cross_validation.train_test_split(word_data, authors, test_size=0.1, random_state=42)
from sklearn.feature_extraction.text import TfidfVectorizer
vectorizer = TfidfVectorizer(sublinear_tf=True, max_df=0.5,
                             stop_words='english')
features_train = vectorizer.fit_transform(features_train)
features_test  = vectorizer.transform(features_test).toarray()

features_train = features_train[:150].toarray()
labels_train   = labels_train[:150]

## Let's do some overfitting: many features, few samples

In [134]:
from sklearn.tree import DecisionTreeClassifier
from sklearn.metrics import accuracy_score
dt = DecisionTreeClassifier()

dt.fit(features_train,labels_train)
labels_predict = dt.predict(features_test)
print 'Accuracy of ' + str(accuracy_score(labels_test,labels_predict)) + ' %'

Accuracy of 0.947667804323 %


## Ok, probably overfitted, so what are the most important features?

In [135]:
import numpy as np
print 'max importance: ' + str(np.max(dt.feature_importances_))
print 'number max importance '+ str(np.argmax(dt.feature_importances_))
print 'max important feature: ' + vectorizer.get_feature_names()[np.argmax(dt.feature_importances_)]

max importance: 0.764705882353
number max importance 33614
max important feature: sshacklensf


## 76% importance: looks shady, lets clean it out

Put this feature in list above and reran from there

In [136]:
extract_rinse_repeat(["sara", "shackleton", "chris", "germani","sshacklensf"])

import numpy
numpy.random.seed(42)
words_file = "your_word_data.pkl" 
authors_file = "your_email_authors.pkl"
word_data = pickle.load( open(words_file, "r"))
authors = pickle.load( open(authors_file, "r") )

from sklearn import cross_validation
features_train, features_test, labels_train, labels_test = cross_validation.train_test_split(word_data, authors, test_size=0.1, random_state=42)
from sklearn.feature_extraction.text import TfidfVectorizer
vectorizer = TfidfVectorizer(sublinear_tf=True, max_df=0.5,
                             stop_words='english')
features_train = vectorizer.fit_transform(features_train)
features_test  = vectorizer.transform(features_test).toarray()

features_train = features_train[:150].toarray()
labels_train   = labels_train[:150]

from sklearn.tree import DecisionTreeClassifier
from sklearn.metrics import accuracy_score
dt = DecisionTreeClassifier()

dt.fit(features_train,labels_train)
labels_predict = dt.predict(features_test)
print 'Accuracy of ' + str(accuracy_score(labels_test,labels_predict)) + ' %'

import numpy as np
print 'max importance: ' + str(np.max(dt.feature_importances_))
print 'number max importance '+ str(np.argmax(dt.feature_importances_))
print 'max important feature: ' + vectorizer.get_feature_names()[np.argmax(dt.feature_importances_)]

C:\Users\dehaeth\Documents\Tools\Python\Oefeningen\Udacity\Machine learning intor\ud120-projects-master\maildir/bailey-s/deleted_items/101.
C:\Users\dehaeth\Documents\Tools\Python\Oefeningen\Udacity\Machine learning intor\ud120-projects-master\maildir/bailey-s/deleted_items/106.
C:\Users\dehaeth\Documents\Tools\Python\Oefeningen\Udacity\Machine learning intor\ud120-projects-master\maildir/bailey-s/deleted_items/132.
C:\Users\dehaeth\Documents\Tools\Python\Oefeningen\Udacity\Machine learning intor\ud120-projects-master\maildir/bailey-s/deleted_items/185.
C:\Users\dehaeth\Documents\Tools\Python\Oefeningen\Udacity\Machine learning intor\ud120-projects-master\maildir/bailey-s/deleted_items/186.
C:\Users\dehaeth\Documents\Tools\Python\Oefeningen\Udacity\Machine learning intor\ud120-projects-master\maildir/bailey-s/deleted_items/187.
C:\Users\dehaeth\Documents\Tools\Python\Oefeningen\Udacity\Machine learning intor\ud120-projects-master\maildir/bailey-s/deleted_items/193.
C:\Users\dehaeth\Doc

## Rinse and repeat, rinse and repeat: clear cgermannsf

In [137]:
extract_rinse_repeat(["sara", "shackleton", "chris", "germani","sshacklensf","cgermannsf"])

import numpy
numpy.random.seed(42)
words_file = "your_word_data.pkl" 
authors_file = "your_email_authors.pkl"
word_data = pickle.load( open(words_file, "r"))
authors = pickle.load( open(authors_file, "r") )

from sklearn import cross_validation
features_train, features_test, labels_train, labels_test = cross_validation.train_test_split(word_data, authors, test_size=0.1, random_state=42)
from sklearn.feature_extraction.text import TfidfVectorizer
vectorizer = TfidfVectorizer(sublinear_tf=True, max_df=0.5,
                             stop_words='english')
features_train = vectorizer.fit_transform(features_train)
features_test  = vectorizer.transform(features_test).toarray()

features_train = features_train[:150].toarray()
labels_train   = labels_train[:150]

from sklearn.tree import DecisionTreeClassifier
from sklearn.metrics import accuracy_score
dt = DecisionTreeClassifier()

dt.fit(features_train,labels_train)
labels_predict = dt.predict(features_test)
print 'Accuracy of ' + str(accuracy_score(labels_test,labels_predict)) + ' %'

import numpy as np
print 'max importance: ' + str(np.max(dt.feature_importances_))
print 'number max importance '+ str(np.argmax(dt.feature_importances_))
print 'max important feature: ' + vectorizer.get_feature_names()[np.argmax(dt.feature_importances_)]

C:\Users\dehaeth\Documents\Tools\Python\Oefeningen\Udacity\Machine learning intor\ud120-projects-master\maildir/bailey-s/deleted_items/101.
C:\Users\dehaeth\Documents\Tools\Python\Oefeningen\Udacity\Machine learning intor\ud120-projects-master\maildir/bailey-s/deleted_items/106.
C:\Users\dehaeth\Documents\Tools\Python\Oefeningen\Udacity\Machine learning intor\ud120-projects-master\maildir/bailey-s/deleted_items/132.
C:\Users\dehaeth\Documents\Tools\Python\Oefeningen\Udacity\Machine learning intor\ud120-projects-master\maildir/bailey-s/deleted_items/185.
C:\Users\dehaeth\Documents\Tools\Python\Oefeningen\Udacity\Machine learning intor\ud120-projects-master\maildir/bailey-s/deleted_items/186.
C:\Users\dehaeth\Documents\Tools\Python\Oefeningen\Udacity\Machine learning intor\ud120-projects-master\maildir/bailey-s/deleted_items/187.
C:\Users\dehaeth\Documents\Tools\Python\Oefeningen\Udacity\Machine learning intor\ud120-projects-master\maildir/bailey-s/deleted_items/193.
C:\Users\dehaeth\Doc